## Exercise : Extracting data from OFET-DB to perform ML

Its great that we have data stored in a standardized manner in our database but now we need to extract data from this database in the form of a table containing descriptors [X] and property [y] to perform ML. This notebook will focus on how we can do that. 

First i want you to use the backup file called 20231206_ofetdb_v2_backup11 and add it to your pgadmin as a practice database. We will avoid working with the original database.

In [1]:
# Connect to the database


import psycopg2
import pandas as pd
import numpy as np
import plotly.express as px


#sample connection details
# pgparams = {
#     "host": "127.0.0.1",
#     "database": "ofetdb_testenv",
#     "user": "postgres",
#     "password": "password",
#     "port": "5432",
# }


# Set max number of displayed columns and rows in Jupyter Notebook
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)


pgparams = {
    "host": "chbe-ofet-db.postgres.database.azure.com",
    "database": "ofetdb_v2_test",
    "user": "mg200_ofetdb",
    "password": "MGEROFETDB23!",
    "port": "5432",
}

def read_select_query(query):

    with psycopg2.connect(**pgparams) as conn:

        df = pd.read_sql_query(query, conn)

    return df


## Simplest Scenario :

- assume only single polymer scenarios, no blends first (wt_frac = 1)
- assume only single solvent scenarios, no multiple solvents (vol_frac = 1)
- show device substrate information 
- show film deposition information (spin, blade, etc). We will not use the parameters for now
- dont go into detail of solution treatment, substrate pretreat and post process. Just show if treatment was performed
- show hole mobility information

Follow the code blocks below and we will eventually end up with a table containing this information 

1. Prepare a dataframe containing the sample_Id, citation_type and meta information from the experimental table (This one is done as a practice for you)

In [2]:
## Adding all the experiment information 

# SQL query to fetch the required data
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id;
'''

# Use the read_select_query function to execute the query
result_df = read_select_query(query)

# Display the resulting DataFrame
#print(result_df)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          13    literature   
13          14    literature   
14          15    literature   
15          16    literature   
16          17    literature   
17          18    literature   
18          19    literature   
19          20    literature   
20          21    literature   
21          22    literature   
22          23    literature   
23          24    literature   
24          25    literature   
25          26    literature   
26          27    literature   
27          28    literature   
28          29    literature   
29          30    literature   
30          31    literature   
31          32    literature   
32          33    literature   
33          34    literature   
34          35    literature   
35          36    literature   
36          37    literature   
37          38    literature   
38          39    literature   
39          40    literature   
40          41    literature   
41          42    literature   
42          43    literature   
43          44    literature   
44          45    literature   
45          46    literature   
46          47    literature   
47          48    literature   
48          49    literature   
49          50    literature   
50          51    literature   
51          52    literature   
52          53    literature   
53          54    literature   
54          55    literature   
55          56    literature   
56          57    literature   
57          58    literature   
58          59    literature   
59          60    literature   
60          61    literature   
61          62    literature   
62          63    literature   
63          64    literature   
64          65    literature   
65          66    literature   
66          67    literature   
67          68    literature   
68          69    literature   
69          70    literature   
70          71    literature   
71          72    literature   
72          73    literature   
73          74    literature   
74          75    literature   
75          76    literature   
76          77    literature   
77          78    literature   
78          79    literature   
79          80    literature   
80          81    literature   
81          82    literature   
82          83    literature   
83          84    literature   
84          85    literature   
85          86    literature   
86          87    literature   
87          88    literature   
88          89    literature   
89          90    literature   
90          91    literature   
91          92    literature   
92          93    literature   
93          94    literature   
94          95    literature   
95          96    literature   
96          97    literature   
97          98    literature   
98          99    literature   
99         100    literature   
100        101    literature   
101        102    literature   
102        103    literature   
103        104    literature   
104        105    literature   
105        106    literature   
106        107    literature   
107        108    literature   
108        109    literature   
109        110    literature   
110        111    literature   
111        112    literature   
112        113    literature   
113        114    literature   
114        115    literature   
115        116    literature   
116        117    literature   
117        118    literature   
118        119    literature   
119        120    literature   
120        121    literature   
121        122    literature   
122        123    literature   
123        124    literature   
124  

remember to keep adding to the existing query to add more information to the table. It is going to get complicated and long soon FYI. 

2. Now to this database add the solution concentration information

In [3]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          13    literature   
13          14    literature   
14          15    literature   
15          16    literature   
16          17    literature   
17          18    literature   
18          19    literature   
19          20    literature   
20          21    literature   
21          22    literature   
22          23    literature   
23          24    literature   
24          25    literature   
25          26    literature   
26          27    literature   
27          28    literature   
28          29    literature   
29          30    literature   
30          31    literature   
31          32    literature   
32          33    literature   
33          34    literature   
34          35    literature   
35          36    literature   
36          37    literature   
37          38    literature   
38          39    literature   
39          40    literature   
40          41    literature   
41          42    literature   
42          43    literature   
43          44    literature   
44          45    literature   
45          46    literature   
46          47    literature   
47          48    literature   
48          49    literature   
49          50    literature   
50          51    literature   
51          52    literature   
52          53    literature   
53          54    literature   
54          55    literature   
55          56    literature   
56          57    literature   
57          58    literature   
58          59    literature   
59          60    literature   
60          61    literature   
61          62    literature   
62          63    literature   
63          64    literature   
64          65    literature   
65          66    literature   
66          67    literature   
67          68    literature   
68          69    literature   
69          70    literature   
70          71    literature   
71          72    literature   
72          73    literature   
73          74    literature   
74          75    literature   
75          76    literature   
76          77    literature   
77          78    literature   
78          79    literature   
79          80    literature   
80          81    literature   
81          82    literature   
82          83    literature   
83          84    literature   
84          85    literature   
85          86    literature   
86          87    literature   
87          88    literature   
88          89    literature   
89          90    literature   
90          91    literature   
91          92    literature   
92          93    literature   
93          94    literature   
94          95    literature   
95          96    literature   
96          97    literature   
97          98    literature   
98          99    literature   
99         100    literature   
100        101    literature   
101        102    literature   
102        103    literature   
103        104    literature   
104        105    literature   
105        106    literature   
106        107    literature   
107        108    literature   
108        109    literature   
109        110    literature   
110        111    literature   
111        112    literature   
112        113    literature   
113        114    literature   
114        115    literature   
115        116    literature   
116        117    literature   
117        118    literature   
118        119    literature   
119        120    literature   
120        121    literature   
121        122    literature   
122        123    literature   
123        124    literature   
124  

3. Now to this table add the solvent information but only consider devices made from single solvent vol frac = 1

In [4]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_fract,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    WHERE
        sms.vol_frac=1;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          13    literature   
13          14    literature   
14          15    literature   
15          16    literature   
16          17    literature   
17          18    literature   
18          19    literature   
19          20    literature   
20          21    literature   
21          22    literature   
22          23    literature   
23          24    literature   
24          25    literature   
25          26    literature   
26          27    literature   
27          28    literature   
28          29    literature   
29          30    literature   
30          31    literature   
31          32    literature   
32          33    literature   
33          34    literature   
34          35    literature   
35          36    literature   
36          37    literature   
37          38    literature   
38          39    literature   
39          40    literature   
40          41    literature   
41          42    literature   
42          43    literature   
43          44    literature   
44          45    literature   
45          46    literature   
46          47    literature   
47          48    literature   
48          49    literature   
49          50    literature   
50          51    literature   
51          52    literature   
52          53    literature   
53          54    literature   
54          55    literature   
55          56    literature   
56          57    literature   
57          58    literature   
58          59    literature   
59          60    literature   
60          61    literature   
61          62    literature   
62          63    literature   
63          64    literature   
64          65    literature   
65          66    literature   
66          67    literature   
67          68    literature   
68          69    literature   
69          70    literature   
70          71    literature   
71          72    literature   
72          73    literature   
73          75    literature   
74          81    literature   
75          82    literature   
76          83    literature   
77          84    literature   
78          85    literature   
79          86    literature   
80          87    literature   
81          88    literature   
82          89    literature   
83          90    literature   
84          91    literature   
85          92    literature   
86          93    literature   
87          94    literature   
88          95    literature   
89          96    literature   
90          97    literature   
91          98    literature   
92          99    literature   
93         100    literature   
94         101    literature   
95         102    literature   
96         103    literature   
97         104    literature   
98         105    literature   
99         106    literature   
100        107    literature   
101        108    literature   
102        109    literature   
103        110    literature   
104        111    literature   
105        112    literature   
106        113    literature   
107        114    literature   
108        115    literature   
109        116    literature   
110        117    literature   
111        118    literature   
112        119    literature   
113        120    literature   
114        121    literature   
115        122    literature   
116        123    literature   
117        124    literature   
118        125    literature   
119        126    literature   
120        127    literature   
121        128    literature   
122        129    literature   
123        130    literature   
124  

4. Now to this table add polymer information only for devices made from one polymer (no blends) (wt-frac = 1)

In [5]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_fract,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER smp ON sol.solution_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    WHERE
        sms.vol_frac=1 AND smp.wt_frac=1;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        144    laboratory   
118        149    laboratory   
119        154    laboratory   
120        159    laboratory   
121        160    laboratory   
122        161    laboratory   
123        162    laboratory   
124  

5. Now to this table add the device substrate information 

In [6]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_fract,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER smp ON sol.solution_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    WHERE
        sms.vol_frac=1 AND smp.wt_frac=1;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        144    laboratory   
118        149    laboratory   
119        154    laboratory   
120        159    laboratory   
121        160    laboratory   
122        161    laboratory   
123        162    laboratory   
124  

6. Now to this table add the film deposition type only not the parameters associated with it

In [7]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_fract,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER smp ON sol.solution_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
    WHERE
        sms.vol_frac=1 AND smp.wt_frac=1;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0            1    literature   
1            2    literature   
2            3    literature   
3            4    literature   
4            5    literature   
5            6    literature   
6            7    literature   
7            8    literature   
8            9    literature   
9           10    literature   
10          11    literature   
11          12    literature   
12          21    literature   
13          22    literature   
14          23    literature   
15          24    literature   
16          25    literature   
17          26    literature   
18          27    literature   
19          28    literature   
20          29    literature   
21          30    literature   
22          31    literature   
23          32    literature   
24          33    literature   
25          34    literature   
26          35    literature   
27          43    literature   
28          44    literature   
29          45    literature   
30          46    literature   
31          47    literature   
32          48    literature   
33          49    literature   
34          50    literature   
35          51    literature   
36          52    literature   
37          53    literature   
38          54    literature   
39          55    literature   
40          56    literature   
41          57    literature   
42          58    literature   
43          59    literature   
44          60    literature   
45          61    literature   
46          62    literature   
47          63    literature   
48          64    literature   
49          65    literature   
50          66    literature   
51          67    literature   
52          68    literature   
53          75    literature   
54          81    literature   
55          82    literature   
56          83    literature   
57          84    literature   
58          85    literature   
59          86    literature   
60          87    literature   
61          88    literature   
62          89    literature   
63          90    literature   
64          91    literature   
65          92    literature   
66          93    literature   
67          94    literature   
68          95    literature   
69          96    literature   
70          97    literature   
71          98    literature   
72          99    literature   
73         100    literature   
74         101    literature   
75         102    literature   
76         103    literature   
77         104    literature   
78         105    literature   
79         106    literature   
80         107    literature   
81         108    literature   
82         109    literature   
83         110    literature   
84         111    literature   
85         112    literature   
86         113    literature   
87         114    literature   
88         115    literature   
89         116    literature   
90         117    literature   
91         118    literature   
92         119    literature   
93         120    literature   
94         121    literature   
95         122    literature   
96         123    literature   
97         124    literature   
98         125    literature   
99         126    literature   
100        127    literature   
101        128    literature   
102        129    literature   
103        130    literature   
104        131    literature   
105        132    literature   
106        133    literature   
107        134    literature   
108        135    literature   
109        136    laboratory   
110        137    laboratory   
111        138    laboratory   
112        139    laboratory   
113        140    laboratory   
114        141    laboratory   
115        142    laboratory   
116        143    laboratory   
117        144    laboratory   
118        149    laboratory   
119        154    laboratory   
120        159    laboratory   
121        160    laboratory   
122        161    laboratory   
123        162    laboratory   
124  

7. Now to this table add the solution treatment, substrate preatreat and post process informaiton 

1 if treatment is done and 0 if no treatment



In [8]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_fract,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params,
        CAST(m.data -> 'electron_mobility' ->> 'value' AS FLOAT) AS electron_mobility

    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER smp ON sol.solution_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
    LEFT JOIN
        MEASUREMENT m on s.sample_id = m.sample_id
    WHERE
        sms.vol_frac=1 AND smp.wt_frac=1 AND
        m.measurement_type = 'transfer_curve' AND
        m.data -> 'electron_
        mobility' ->> 'value' IS NOT NULL;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


Empty DataFrame
Columns: [sample_id, citation_type, experiment_meta, concentration, solvent_vol_fract, solvent_pubchem_cid, solvent_iupac_name, polymer_common_name, polymer_iupac_name, polymer_mw, polymer_mn, polymer_dispersity, device_substrate_parameters, film_deposition_type, film_deposition_params, electron_mobility]
Index: []

8. Now to this table add the hole mobility information 

only keep devices that have an actual hole mobility value and is not Null or NAN

In [2]:
query = '''
    SELECT
        s.sample_id,
        e.citation_type,
        e.meta as experiment_meta,
        sol.concentration,
        sms.vol_frac as solvent_vol_frac,
        sv.pubchem_cid as solvent_pubchem_cid,
        sv.iupac_name as solvent_iupac_name,
        p.common_name as polymer_common_name,
        p.iupac_name as polymer_iupac_name,
        p.mw as polymer_mw,
        p.mn as polymer_mn,
        p.dispersity as polymer_dispersity,
        df.params as device_substrate_parameters,
        fd.deposition_type as film_deposition_type,
        fd.params as film_deposition_params,
        CAST(m.data -> 'electron_mobility' ->> 'value' AS FLOAT) AS electron_mobility,
        CASE WHEN op.solution_treatment_id IS NOT NULL THEN 1 ELSE 0 END AS Solution_treatment,
        CASE WHEN op.substrate_pretreat_id is NOT NULL THEN 1 ELSE 0 END AS Substrate_pretreatment,
        CASE WHEN op.postprocess_id IS NOT NULL THEN 1 ELSE 0 END AS Post_process
    FROM
        SAMPLE as s
    JOIN
        EXPERIMENT_INFO as e ON s.exp_id = e.exp_id
    LEFT JOIN
        OFET_PROCESS op ON s.process_id = op.process_id
    LEFT JOIN
        SOLUTION sol ON op.solution_id = sol.solution_id
    LEFT JOIN
        SOLUTION_MAKEUP_SOLVENT sms ON sol.solution_id = sms.solution_id
    LEFT JOIN
        SOLVENT sv ON sms.solvent_id = sv.pubchem_cid
    LEFT JOIN
        SOLUTION_MAKEUP_POLYMER smp ON sol.solution_id = smp.solution_id
    LEFT JOIN
        POLYMER p ON smp.polymer_id = p.polymer_id
    LEFT JOIN
        DEVICE_FABRICATION df ON op.device_fab_id = df.device_fab_id
    LEFT JOIN
        FILM_DEPOSITION fd ON op.film_deposition_id = fd.film_deposition_id
    LEFT JOIN
        MEASUREMENT m on s.sample_id = m.sample_id
    WHERE
        sms.vol_frac=1 AND smp.wt_frac=1 AND
        m.measurement_type = 'transfer_curve' AND
        m.data -> 'electron_mobility' ->> 'value' IS NOT NULL;
'''

result_df = read_select_query(query)

result_df

C:\Users\Myeongyeon Lee\anaconda3\lib\site-packages\pandas\io\sql.py:761: UserWarning: pandas only support SQLAlchemy connectable(engine/connection) ordatabase string URI or sqlite3 DBAPI2 connectionother DBAPI2 objects are not tested, please consider using SQLAlchemy
  warnings.warn(


sample_id citation_type  \
0          666    laboratory   
1          670    laboratory   
2          125    literature   
3          661    laboratory   
4           24    literature   
5           25    literature   
6           26    literature   
7           27    literature   
8           28    literature   
9           29    literature   
10          30    literature   
11          31    literature   
12          32    literature   
13          33    literature   
14          34    literature   
15          51    literature   
16          52    literature   
17          53    literature   
18          54    literature   
19          75    literature   
20          81    literature   
21          82    literature   
22         126    literature   
23         127    literature   
24         128    literature   
25         179    literature   
26         180    literature   
27         181    literature   
28         182    literature   
29         183    literature   
30         184    literature   
31         185    literature   
32         186    literature   
33         187    literature   
34         188    literature   
35         189    literature   
36         190    literature   
37         191    literature   
38         192    literature   
39         193    literature   
40         194    literature   
41         195    literature   
42         196    literature   
43         197    literature   
44         198    literature   
45         199    literature   
46         200    literature   
47         201    literature   
48         202    literature   
49         203    literature   
50         204    literature   
51         205    literature   
52         206    literature   
53         235    literature   
54         208    literature   
55         209    literature   
56         210    literature   
57         211    literature   
58         212    literature   
59         213    literature   
60         214    literature   
61         215    literature   
62         216    literature   
63         217    literature   
64         218    literature   
65         219    literature   
66         220    literature   
67         221    literature   
68         222    literature   
69         223    literature   
70         224    literature   
71         225    literature   
72         226    literature   
73         227    literature   
74         228    literature   
75         242    literature   
76         243    literature   
77         244    literature   
78         245    literature   
79         246    literature   
80         247    literature   
81         248    literature   
82         249    literature   
83         250    literature   
84         264    literature   
85         265    literature   
86         266    literature   
87         267    literature   
88         268    literature   
89         269    literature   
90         270    literature   
91         271    literature   
92         272    literature   
93         273    literature   
94         274    literature   
95         275    literature   
96         276    literature   
97         277    literature   
98         278    literature   
99         662    laboratory   
100        667    laboratory   
101        287    literature   
102        300    literature   
103        313    literature   
104        318    literature   
105        323    literature   
106        328    literature   
107        329    literature   
108        330    literature   
109        331    literature   
110        332    literature   
111        333    literature   
112        334    literature   
113        663    laboratory   
114        664    laboratory   
115        668    laboratory   
116        570    literature   
117        571    literature   
118        572    literature   
119        573    literature   
120        574    literature   
121        575    literature   
122        576    literature   
123        577    literature   
124  

This is a simple version of the dataframe result_df. There are a couple more things we can now do to the dataframe to make it more machine readable. We no longer need to use sql queries. can just work with the dataframe and pandas

9. The code block below will unpack the data stored in device_substrate_parameters and store it as columns (this one is done for you)

In [3]:
 #unpacking the information stored in device_substrate_parameters

import pandas as pd
from pandas import json_normalize

# # Extract the 'device_substrate_parameters' column and normalize it
params_df = json_normalize(result_df['device_substrate_parameters'])

# # Concatenate the original DataFrame with the new 'params_df'
result_df = pd.concat([result_df, params_df], axis=1)

# # Drop the original 'device_substrate_parameters' column
result_df = result_df.drop('device_substrate_parameters', axis=1)

# # Display the resulting DataFrame
result_df

sample_id citation_type  \
0          666    laboratory   
1          670    laboratory   
2          125    literature   
3          661    laboratory   
4           24    literature   
5           25    literature   
6           26    literature   
7           27    literature   
8           28    literature   
9           29    literature   
10          30    literature   
11          31    literature   
12          32    literature   
13          33    literature   
14          34    literature   
15          51    literature   
16          52    literature   
17          53    literature   
18          54    literature   
19          75    literature   
20          81    literature   
21          82    literature   
22         126    literature   
23         127    literature   
24         128    literature   
25         179    literature   
26         180    literature   
27         181    literature   
28         182    literature   
29         183    literature   
30         184    literature   
31         185    literature   
32         186    literature   
33         187    literature   
34         188    literature   
35         189    literature   
36         190    literature   
37         191    literature   
38         192    literature   
39         193    literature   
40         194    literature   
41         195    literature   
42         196    literature   
43         197    literature   
44         198    literature   
45         199    literature   
46         200    literature   
47         201    literature   
48         202    literature   
49         203    literature   
50         204    literature   
51         205    literature   
52         206    literature   
53         235    literature   
54         208    literature   
55         209    literature   
56         210    literature   
57         211    literature   
58         212    literature   
59         213    literature   
60         214    literature   
61         215    literature   
62         216    literature   
63         217    literature   
64         218    literature   
65         219    literature   
66         220    literature   
67         221    literature   
68         222    literature   
69         223    literature   
70         224    literature   
71         225    literature   
72         226    literature   
73         227    literature   
74         228    literature   
75         242    literature   
76         243    literature   
77         244    literature   
78         245    literature   
79         246    literature   
80         247    literature   
81         248    literature   
82         249    literature   
83         250    literature   
84         264    literature   
85         265    literature   
86         266    literature   
87         267    literature   
88         268    literature   
89         269    literature   
90         270    literature   
91         271    literature   
92         272    literature   
93         273    literature   
94         274    literature   
95         275    literature   
96         276    literature   
97         277    literature   
98         278    literature   
99         662    laboratory   
100        667    laboratory   
101        287    literature   
102        300    literature   
103        313    literature   
104        318    literature   
105        323    literature   
106        328    literature   
107        329    literature   
108        330    literature   
109        331    literature   
110        332    literature   
111        333    literature   
112        334    literature   
113        663    laboratory   
114        664    laboratory   
115        668    laboratory   
116        570    literature   
117        571    literature   
118        572    literature   
119        573    literature   
120        574    literature   
121        575    literature   
122        576    literature   
123        577    literature   
124  

In [4]:

# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['film_deposition_params', 'citation_type', 'experiment_meta', 'solvent_vol_frac', 'solvent_iupac_name', 'polymer_iupac_name', 'dielectric_material_2', 'dielectric_thickness_2', 'dielectric_1_material', 'dielectric_1_thickness']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  concentration  solvent_pubchem_cid polymer_common_name  \
0          666           6.00                 7964               N2200   
1          670          10.00                 7964               N2200   
2          125          10.00                 7239             DPP-DTT   
3          661           1.00                 7964               N2200   
4           24           5.00                 7964             DPP-DTT   
5           25           5.00                 7964             DPP-DTT   
6           26           5.00                 7964             DPP-DTT   
7           27           5.00                 7964             DPP-DTT   
8           28           5.00                 7964             DPP-DTT   
9           29           5.00                 7964             DPP-DTT   
10          30           5.00                 7964             DPP-DTT   
11          31           5.00                 7964             DPP-DTT   
12          32           5.00                 7964             DPP-DTT   
13          33           5.00                 7964             DPP-DTT   
14          34           5.00                 7964             DPP-DTT   
15          51           3.00                 7239             DPP-DTT   
16          52           3.00                 7239             DPP-DTT   
17          53           7.00                 7239             DPP-DTT   
18          54           7.00                 7239             DPP-DTT   
19          75           4.00                 6212             DPP-DTT   
20          81           5.00                 6212             DPP-DTT   
21          82           5.00                 6212             DPP-DTT   
22         126          10.00                 7239             DPP-DTT   
23         127          10.00                 7239             DPP-DTT   
24         128          10.00                 7239             DPP-DTT   
25         179           7.00                 6591               N2200   
26         180           3.00                 6591               N2200   
27         181           1.00                 6591               N2200   
28         182           0.50                 6591               N2200   
29         183           8.00                 7239               N2200   
30         184           7.00                 6591               N2200   
31         185           3.00                 6591               N2200   
32         186           1.00                 6591               N2200   
33         187           8.00                 7239               N2200   
34         188           7.00                 6591               N2200   
35         189           3.00                 6591               N2200   
36         190           1.00                 6591               N2200   
37         191           0.50                 6591               N2200   
38         192           9.00                 7239               N2200   
39         193           9.00                 7239               N2200   
40         194           9.00                 7239               N2200   
41         195           9.00                 7239               N2200   
42         196           9.00                 7239               N2200   
43         197           9.00                 7239               N2200   
44         198           9.00                 7239               N2200   
45         199           9.00                 7239               N2200   
46         200           9.00                 7239               N2200   
47         201           9.00                 7239               N2200   
48         202           9.00                 7239               N2200   
49         203           9.00                 7239               N2200   
50         204           9.00                 7239               N2200   
51         205           9.00                 7239               N2200   
52         206           9.00                 7239               N2200   
53       

We are now going to do something called one hot encoding to convert columns with textual information into numbers (1 and 0)

In [5]:
# List of columns to one-hot encode
columns_to_one_hot_encode = ['film_deposition_type', 'gate_material', 'dielectric_material', 'electrode_configuration']

# Perform one-hot encoding
result_df = pd.get_dummies(result_df, columns=columns_to_one_hot_encode)

# Display the resulting DataFrame with one-hot encoding
result_df


sample_id  concentration  solvent_pubchem_cid polymer_common_name  \
0          666           6.00                 7964               N2200   
1          670          10.00                 7964               N2200   
2          125          10.00                 7239             DPP-DTT   
3          661           1.00                 7964               N2200   
4           24           5.00                 7964             DPP-DTT   
5           25           5.00                 7964             DPP-DTT   
6           26           5.00                 7964             DPP-DTT   
7           27           5.00                 7964             DPP-DTT   
8           28           5.00                 7964             DPP-DTT   
9           29           5.00                 7964             DPP-DTT   
10          30           5.00                 7964             DPP-DTT   
11          31           5.00                 7964             DPP-DTT   
12          32           5.00                 7964             DPP-DTT   
13          33           5.00                 7964             DPP-DTT   
14          34           5.00                 7964             DPP-DTT   
15          51           3.00                 7239             DPP-DTT   
16          52           3.00                 7239             DPP-DTT   
17          53           7.00                 7239             DPP-DTT   
18          54           7.00                 7239             DPP-DTT   
19          75           4.00                 6212             DPP-DTT   
20          81           5.00                 6212             DPP-DTT   
21          82           5.00                 6212             DPP-DTT   
22         126          10.00                 7239             DPP-DTT   
23         127          10.00                 7239             DPP-DTT   
24         128          10.00                 7239             DPP-DTT   
25         179           7.00                 6591               N2200   
26         180           3.00                 6591               N2200   
27         181           1.00                 6591               N2200   
28         182           0.50                 6591               N2200   
29         183           8.00                 7239               N2200   
30         184           7.00                 6591               N2200   
31         185           3.00                 6591               N2200   
32         186           1.00                 6591               N2200   
33         187           8.00                 7239               N2200   
34         188           7.00                 6591               N2200   
35         189           3.00                 6591               N2200   
36         190           1.00                 6591               N2200   
37         191           0.50                 6591               N2200   
38         192           9.00                 7239               N2200   
39         193           9.00                 7239               N2200   
40         194           9.00                 7239               N2200   
41         195           9.00                 7239               N2200   
42         196           9.00                 7239               N2200   
43         197           9.00                 7239               N2200   
44         198           9.00                 7239               N2200   
45         199           9.00                 7239               N2200   
46         200           9.00                 7239               N2200   
47         201           9.00                 7239               N2200   
48         202           9.00                 7239               N2200   
49         203           9.00                 7239               N2200   
50         204           9.00                 7239               N2200   
51         205           9.00                 7239               N2200   
52         206           9.00                 7239               N2200   
53       

Now lets see all the columns in this database 

In [10]:
column_names = result_df.columns
print(column_names)

Index(['sample_id', 'concentration', 'solvent_pubchem_cid',
       'polymer_common_name', 'polymer_mw', 'polymer_mn', 'polymer_dispersity',
       'electron_mobility', 'solution_treatment', 'substrate_pretreatment',
       'post_process', 'channel_width', 'channel_length',
       'dielectric_thickness', 'film_deposition_type_blade',
       'film_deposition_type_drop', 'film_deposition_type_inkjet',
       'film_deposition_type_spin', 'film_deposition_type_water',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4', 'dielectric_material_SiO2',
       'electrode_configuration_BGBC', 'electrode_configuration_BGTC',
       'electrode_configuration_TGBC', 'gate_material_Si',
       'gate_material_Other'],
      dtype='object')


### Consolidating Descriptors

We are going to consolidate some of the descriptors into one column. 


Coating :

* film_deposition_type_MGC (dip,Dip,blade, inkjet, shear, wire) - value of 1 if any of these columns are true or else 0
* film_deposition_type_spin
* film_deposition_type_drop

Gate Material :

* gate_material_n_doped Si = ('gate_material_n-doped Si', 'gate_material_Si','gate_material_p-doped Si') 

* gate_material_other = ('gate_material_Al', 'gate_material_Au', 'gate_material_PEDOT:PSS', 'gate_material_PET','gate_material_glass')


Dielectric Material :

* dielectric_material_SiO2
* dielectric_material_other = (
        'dielectric_material_6FDA-DABC',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4')




In [9]:

#consolidating gate material columns
gate_material_Si_to_consolidate = ['gate_material_n-doped Si','gate_material_p-doped Si']
gate_material_other_to_consolidate = ['gate_material_Al', 'gate_material_Au', 'gate_material_Cu', 'gate_material_PET','gate_material_glass']
# Create new columns
result_df['gate_material_Si'] = result_df[gate_material_Si_to_consolidate].max(axis=1)
result_df['gate_material_Other'] = result_df[gate_material_other_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=gate_material_Si_to_consolidate, inplace=True)
result_df.drop(columns=gate_material_other_to_consolidate, inplace=True)


#consolidating coating columns
MGC_columns_to_consolidate = ['film_deposition_type_blade',
                           'film_deposition_type_inkjet']
# Create new columns
result_df['film_deposition_type_MGC'] = result_df[MGC_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=MGC_columns_to_consolidate, inplace=True)


#consolidating dielectric columns
dielectric_material_columns_to_consolidate = ['dielectric_material_CYTOP','dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_Shellac', 'dielectric_material_Si3N4',
       'dielectric_material_SiO2']
# Create new columns
result_df['dielectric_material_other'] = result_df[dielectric_material_columns_to_consolidate].max(axis=1)
# Drop the original columns
result_df.drop(columns=dielectric_material_columns_to_consolidate, inplace=True)


KeyError: "None of [Index(['gate_material_n-doped Si', 'gate_material_p-doped Si'], dtype='object')] are in the [columns]"

In [14]:
result_df

sample_id  concentration  solvent_pubchem_cid polymer_common_name  \
0          666           6.00                 7964               N2200   
1          670          10.00                 7964               N2200   
2          125          10.00                 7239             DPP-DTT   
3          661           1.00                 7964               N2200   
4           24           5.00                 7964             DPP-DTT   
5           25           5.00                 7964             DPP-DTT   
6           26           5.00                 7964             DPP-DTT   
7           27           5.00                 7964             DPP-DTT   
8           28           5.00                 7964             DPP-DTT   
9           29           5.00                 7964             DPP-DTT   
10          30           5.00                 7964             DPP-DTT   
11          31           5.00                 7964             DPP-DTT   
12          32           5.00                 7964             DPP-DTT   
13          33           5.00                 7964             DPP-DTT   
14          34           5.00                 7964             DPP-DTT   
15          51           3.00                 7239             DPP-DTT   
16          52           3.00                 7239             DPP-DTT   
17          53           7.00                 7239             DPP-DTT   
18          54           7.00                 7239             DPP-DTT   
19          75           4.00                 6212             DPP-DTT   
20          81           5.00                 6212             DPP-DTT   
21          82           5.00                 6212             DPP-DTT   
22         126          10.00                 7239             DPP-DTT   
23         127          10.00                 7239             DPP-DTT   
24         128          10.00                 7239             DPP-DTT   
25         179           7.00                 6591               N2200   
26         180           3.00                 6591               N2200   
27         181           1.00                 6591               N2200   
28         182           0.50                 6591               N2200   
29         183           8.00                 7239               N2200   
30         184           7.00                 6591               N2200   
31         185           3.00                 6591               N2200   
32         186           1.00                 6591               N2200   
33         187           8.00                 7239               N2200   
34         188           7.00                 6591               N2200   
35         189           3.00                 6591               N2200   
36         190           1.00                 6591               N2200   
37         191           0.50                 6591               N2200   
38         192           9.00                 7239               N2200   
39         193           9.00                 7239               N2200   
40         194           9.00                 7239               N2200   
41         195           9.00                 7239               N2200   
42         196           9.00                 7239               N2200   
43         197           9.00                 7239               N2200   
44         198           9.00                 7239               N2200   
45         199           9.00                 7239               N2200   
46         200           9.00                 7239               N2200   
47         201           9.00                 7239               N2200   
48         202           9.00                 7239               N2200   
49         203           9.00                 7239               N2200   
50         204           9.00                 7239               N2200   
51         205           9.00                 7239               N2200   
52         206           9.00                 7239               N2200   
53       

In [15]:
## replacing the pubchem_cid with solvent boiling point

# Get unique PubChem CIDs from the 'solvent_pubchem_cid' column
unique_pubchem_cids = result_df['solvent_pubchem_cid'].unique()

# Display the unique PubChem CIDs
print(unique_pubchem_cids)



[7964 7239 6212 6591 1140 7809 7003 7947]


In [16]:
# Dictionary mapping PubChem CIDs to boiling points
boiling_point_dict = {
    7964: 132,
    6212: 62,
    7239: 180.1,
    6591: 146,
    7809: 138,
    1140: 111,
    7947: 164.7,
    7003: 259.3
}

# Add a new column "solvent_boiling_point" based on PubChem CIDs
result_df['solvent_boiling_point'] = result_df['solvent_pubchem_cid'].map(boiling_point_dict)


# Drop unnecessary columns that won't be used for modeling
columns_to_drop = ['solvent_pubchem_cid']
result_df = result_df.drop(columns=columns_to_drop)

# Display the resulting DataFrame
result_df


sample_id  concentration polymer_common_name  polymer_mw  polymer_mn  \
0          666           6.00               N2200      202.00        91.0   
1          670          10.00               N2200      202.00        91.0   
2          125          10.00             DPP-DTT      193.50        50.0   
3          661           1.00               N2200      202.00        91.0   
4           24           5.00             DPP-DTT      501.00       110.0   
5           25           5.00             DPP-DTT      501.00       110.0   
6           26           5.00             DPP-DTT      501.00       110.0   
7           27           5.00             DPP-DTT      501.00       110.0   
8           28           5.00             DPP-DTT      501.00       110.0   
9           29           5.00             DPP-DTT      501.00       110.0   
10          30           5.00             DPP-DTT      501.00       110.0   
11          31           5.00             DPP-DTT      501.00       110.0   
12          32           5.00             DPP-DTT      501.00       110.0   
13          33           5.00             DPP-DTT      501.00       110.0   
14          34           5.00             DPP-DTT      501.00       110.0   
15          51           3.00             DPP-DTT      290.00       143.0   
16          52           3.00             DPP-DTT      290.00       143.0   
17          53           7.00             DPP-DTT      290.00       143.0   
18          54           7.00             DPP-DTT      290.00       143.0   
19          75           4.00             DPP-DTT      350.00       125.0   
20          81           5.00             DPP-DTT         NaN         NaN   
21          82           5.00             DPP-DTT         NaN         NaN   
22         126          10.00             DPP-DTT      193.50        50.0   
23         127          10.00             DPP-DTT      193.50        50.0   
24         128          10.00             DPP-DTT      193.50        50.0   
25         179           7.00               N2200       23.00        12.0   
26         180           3.00               N2200       23.00        12.0   
27         181           1.00               N2200       23.00        12.0   
28         182           0.50               N2200       23.00        12.0   
29         183           8.00               N2200       72.00        22.5   
30         184           7.00               N2200       72.00        22.5   
31         185           3.00               N2200       72.00        22.5   
32         186           1.00               N2200       72.00        22.5   
33         187           8.00               N2200      250.00       108.7   
34         188           7.00               N2200      250.00       108.7   
35         189           3.00               N2200      250.00       108.7   
36         190           1.00               N2200      250.00       108.7   
37         191           0.50               N2200      250.00       108.7   
38         192           9.00               N2200       14.00        10.0   
39         193           9.00               N2200       14.00        10.0   
40         194           9.00               N2200       14.00        10.0   
41         195           9.00               N2200       38.00        17.0   
42         196           9.00               N2200       38.00        17.0   
43         197           9.00               N2200       38.00        17.0   
44         198           9.00               N2200       91.00        30.0   
45         199           9.00               N2200       91.00        30.0   
46         200           9.00               N2200       91.00        30.0   
47         201           9.00               N2200      124.00        35.0   
48         202           9.00               N2200      124.00        35.0   
49         203           9.00               N2200      124.00        35.0   
50         204           9.00               N2200      123.00        41.0   
5

In [17]:
column_names = result_df.columns
print(column_names)

Index(['sample_id', 'concentration', 'polymer_common_name', 'polymer_mw',
       'polymer_mn', 'polymer_dispersity', 'electron_mobility',
       'solution_treatment', 'substrate_pretreatment', 'post_process',
       'channel_width', 'channel_length', 'dielectric_thickness',
       'film_deposition_type_blade', 'film_deposition_type_drop',
       'film_deposition_type_inkjet', 'film_deposition_type_spin',
       'film_deposition_type_water', 'gate_material_Al', 'gate_material_Au',
       'gate_material_Cu', 'gate_material_PET', 'gate_material_glass',
       'gate_material_n-doped Si', 'gate_material_p-doped Si',
       'dielectric_material_CYTOP', 'dielectric_material_PAN',
       'dielectric_material_PMMA', 'dielectric_material_PTrFE',
       'dielectric_material_PVP', 'dielectric_material_Shellac',
       'dielectric_material_Si3N4', 'dielectric_material_SiO2',
       'electrode_configuration_BGBC', 'electrode_configuration_BGTC',
       'electrode_configuration_TGBC', 'solvent_boilin

In [18]:
#result_df_P3HT = result_df[result_df['polymer_common_name'] == 'P3HT']
#result_df_DPP_DTT = result_df[result_df['polymer_common_name'] != 'P3HT']
result_df_N2200 = result_df[result_df['polymer_common_name'] == 'N2200']

### P3HT Modeling

In [19]:
result_df_P3HT = result_df_P3HT.drop(columns='polymer_common_name')
result_df_P3HT

NameError: name 'result_df_P3HT' is not defined

In [ ]:
num_rows, num_columns = result_df_P3HT.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")


### N2200 Modeling

In [20]:
result_df_N2200 = result_df_N2200.drop(columns='polymer_common_name')
result_df_N2200

sample_id  concentration  polymer_mw  polymer_mn  polymer_dispersity  \
0          666           6.00      202.00        91.0                2.22   
1          670          10.00      202.00        91.0                2.22   
3          661           1.00      202.00        91.0                2.22   
25         179           7.00       23.00        12.0                1.90   
26         180           3.00       23.00        12.0                1.90   
27         181           1.00       23.00        12.0                1.90   
28         182           0.50       23.00        12.0                1.90   
29         183           8.00       72.00        22.5                3.20   
30         184           7.00       72.00        22.5                3.20   
31         185           3.00       72.00        22.5                3.20   
32         186           1.00       72.00        22.5                3.20   
33         187           8.00      250.00       108.7                2.30   
34         188           7.00      250.00       108.7                2.30   
35         189           3.00      250.00       108.7                2.30   
36         190           1.00      250.00       108.7                2.30   
37         191           0.50      250.00       108.7                2.30   
38         192           9.00       14.00        10.0                1.40   
39         193           9.00       14.00        10.0                1.40   
40         194           9.00       14.00        10.0                1.40   
41         195           9.00       38.00        17.0                2.23   
42         196           9.00       38.00        17.0                2.23   
43         197           9.00       38.00        17.0                2.23   
44         198           9.00       91.00        30.0                3.03   
45         199           9.00       91.00        30.0                3.03   
46         200           9.00       91.00        30.0                3.03   
47         201           9.00      124.00        35.0                3.50   
48         202           9.00      124.00        35.0                3.50   
49         203           9.00      124.00        35.0                3.50   
50         204           9.00      123.00        41.0                3.00   
51         205           9.00      123.00        41.0                3.00   
52         206           9.00      123.00        41.0                3.00   
53         235           8.00         NaN         NaN                 NaN   
54         208          15.00         NaN         NaN                 NaN   
55         209           3.75         NaN         NaN                 NaN   
56         210           7.50         NaN         NaN                 NaN   
57         211           7.50         NaN         NaN                 NaN   
58         212          15.00         NaN         NaN                 NaN   
59         213          10.00         NaN         NaN                 NaN   
60         214          10.00         NaN         NaN                 NaN   
61         215          10.00         NaN         NaN                 NaN   
62         216          10.00         NaN         NaN                 NaN   
63         217          10.00         NaN         NaN                 NaN   
64         218          10.00         NaN         NaN                 NaN   
65         219          10.00         NaN         NaN                 NaN   
66         220          10.00         NaN         NaN                 NaN   
67         221          10.00         NaN         NaN                 NaN   
68         222          10.00         NaN         NaN                 NaN   
69         223           2.00       26.60        15.2                1.75   
70         224           2.00       50.43        20.5                2.46   
71         225           2.00       99.50        48.3                2.06   
72         226           2.00      236.00       103.5                2.28   
7

In [21]:
num_rows, num_columns = result_df_N2200.shape
print(f"Number of rows: {num_rows}")
print(f"Number of columns: {num_columns}")

Number of rows: 104
Number of columns: 36


In [22]:
result_df_N2200.to_excel('result_df_N2200_test.xlsx', index=True, header=True)